In [1]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 485.4/485.4 kB 33.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 14.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 18.4 MB/s eta 0:00:00


In [16]:
from datasets import load_dataset

dataset = load_dataset("cfilt/iitb-english-hindi")["test"]  # English-Hindi dataset
print(dataset)


Dataset({
    features: ['translation'],
    num_rows: 2507
})


In [17]:
from transformers import MarianMTModel, MarianTokenizer

model_name = "Helsinki-NLP/opus-mt-en-hi"  # Change to "opus-mt-hi-en" for Hindi to English
model = MarianMTModel.from_pretrained(model_name)
tokenizer = MarianTokenizer.from_pretrained(model_name)

/usr/local/lib/python3.11/dist-packages/transformers/models/marian/tokenization_marian.py:175: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")


In [18]:
en=[]
hi=[]
for i in dataset['translation']:
  en.append(i["en"])
  hi.append(i["hi"])

In [19]:
en[0],hi[0]

('A black box in your car?', 'आपकी कार में ब्लैक बॉक्स?')

In [20]:
import pandas as pd
df=pd.DataFrame({'en':en,'hi':hi})
df.drop(index=0, inplace=True)
df.head()


en  \
1  As America's road planners struggle to find th...   
2  The devices, which track every mile a motorist...   
3  The usually dull arena of highway planning has...   
4  Libertarians have joined environmental groups ...   
5                           The tea party is aghast.   

                                                  hi  
1  जबकि अमेरिका के सड़क योजनाकार, ध्वस्त होते हुए...  
2  यह डिवाइस, जो मोटर-चालक द्वारा वाहन चलाए गए प्...  
3  आम तौर पर हाईवे नियोजन जैसा उबाऊ काम भी अचानक ...  
4  आपने द्वारा ड्राइव किए गए मील, तथा संभवतः ड्रा...  
5                             चाय पार्टी भौचक्की है।

In [21]:
from sklearn.model_selection import train_test_split
train,test=train_test_split(df,test_size=0.2,random_state=42)
train.reset_index(drop=True,inplace=True)
test.reset_index(drop=True,inplace=True)
train.head(),test.head()

(                                                  en  \
 0  Renamo wanted to "warn the international commu...   
 1  On the occasion of Mahavir Jayanti, the god Ha...   
 2  Already the stamp duty take for residential pr...   
 3  But as the evening comes, our minds change and...   
 4                          "No," Mr Tripodi replied.   
 
                                                   hi  
 0  रे नमो  "चीजें मोजाम्बिक में अच्छी तरह से नहीं...  
 1  देविका तट पर महावीर जयंती के उपलक्ष्य पर भगवान...  
 2  कर वर्ष 2012/13 में वेस्टमिन्स्टर तथा केन्सिंग...  
 3  लेकिन शाम होते ही हमारा मन बदल जाता हैं और हम ...  
 4               "नहीं," श्री त्रिपोडी ने उत्तर दिया।  ,
                                                   en  \
 0  Due to financial constraints Dhirubhai had to ...   
 1  Other places are hoping to sell the concept to...   
 2  There's also money for walk-in clinics in Hoba...   
 3              He wanted the party to become strong.   
 4       It was simply nothing I c

In [22]:
source_train=train['en']
target_train=train['hi']
source_test=test['en']
target_test=test['hi']



In [23]:
source_texts = [ex for ex in train['en']]
source_texts[0]

'Renamo wanted to "warn the international community that things were not going well in Mozambique," Mr Mazanga said.'

In [24]:
def preprocess_function(examples):
    source_texts = examples['en']
    target_texts = examples['hi']

    model_inputs = tokenizer(source_texts.tolist(), truncation=True, padding="max_length", max_length=128)
    labels = tokenizer(target_texts.tolist(), truncation=True, padding="max_length", max_length=128)
    model_inputs["labels"] = labels["input_ids"]

    return model_inputs

tokenized_train = preprocess_function(train)
tokenized_test = preprocess_function(test)


In [25]:
# tokenized_train[0]

In [26]:
print(len(tokenized_train["input_ids"]))
print(len(tokenized_train['attention_mask']))
print(len(tokenized_train["labels"]))
print(len(tokenized_test["input_ids"]))
print(len(tokenized_test['attention_mask']))
print(len(tokenized_test["labels"]))

2004
2004
2004
502
502
502


In [27]:
from datasets import Dataset
tokenized_train_dataset = Dataset.from_dict(tokenized_train)
tokenized_test_dataset = Dataset.from_dict(tokenized_test)

In [28]:
from transformers import TrainingArguments

training_args = TrainingArguments(
    output_dir="./translator_en_hi",
    evaluation_strategy="epoch",
    save_strategy="epoch",
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=1,
    learning_rate=5e-5,
    weight_decay=0.01,
    logging_dir="./logs",
    logging_steps=500,
    save_total_limit=2,
    load_best_model_at_end=True,
)


/usr/local/lib/python3.11/dist-packages/transformers/training_args.py:1575: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [29]:
from transformers import Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_train_dataset,
    eval_dataset=tokenized_test_dataset
)
trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: mummina-premkumar (mummina-premkumar-yami-technology) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


/usr/local/lib/python3.11/dist-packages/transformers/modeling_utils.py:2758: UserWarning: Moving the following attributes in the config to the generation config: {'max_length': 512, 'num_beams': 4, 'bad_words_ids': [[61949]]}. You are seeing this warning because you've set generation parameters in the model config, as opposed to in the generation config.
  warnings.warn(
There were missing keys in the checkpoint model loaded: ['model.encoder.embed_tokens.weight', 'model.encoder.embed_positions.weight', 'model.decoder.embed_tokens.weight', 'model.decoder.embed_positions.weight', 'lm_head.weight'].


TrainOutput(global_step=251, training_loss=2.212838830225971, metrics={'train_runtime': 45.16, 'train_samples_per_second': 44.376, 'train_steps_per_second': 5.558, 'total_flos': 67932323315712.0, 'train_loss': 2.212838830225971, 'epoch': 1.0})

In [30]:
def translate(text, src_lang="en", tgt_lang="hi"):
    inputs = tokenizer(text, return_tensors="pt")
    # Move inputs to the same device as the model
    # Assuming model is on cuda:0 or default cuda device
    for k in inputs:
      inputs[k] = inputs[k].to(model.device)
    translated_tokens = model.generate(**inputs, max_length=50)
    return tokenizer.decode(translated_tokens[0], skip_special_tokens=True)

print(translate("good man"))

अच्छा आदमी


In [33]:
save_directory = "translate_model"

model.save_pretrained(save_directory)

tokenizer.save_pretrained(save_directory)

('translate_model/tokenizer_config.json',
 'translate_model/special_tokens_map.json',
 'translate_model/vocab.json',
 'translate_model/source.spm',
 'translate_model/target.spm',
 'translate_model/added_tokens.json')

In [35]:
import shutil


folder_path = "/content/translate_model"
zip_name = "translate_model_finetune.zip"


shutil.make_archive(zip_name.replace('.zip', ''), 'zip', folder_path)

print(f"Folder '{folder_path}' has been zipped as '{zip_name}'.")

Folder '/content/translate_model' has been zipped as 'translate_model_finetune.zip'.
